# example

In [1]:
MODEL_NAME = "gaepago-20-lite"
DATASET_NAME = "Gae8J/modeling_v1"

## load dataset (test data)

In [2]:
from datasets import load_dataset, Audio
from transformers import AutoFeatureExtractor
dataset = load_dataset(DATASET_NAME)
dataset = dataset.cast_column("audio", Audio(sampling_rate=16000))
test_data = dataset['test']
sampling_rate = test_data.features["audio"].sampling_rate
feature_extractor = AutoFeatureExtractor.from_pretrained(MODEL_NAME)

  0%|          | 0/3 [00:00<?, ?it/s]

In [7]:
from transformers import AutoConfig
config = AutoConfig.from_pretrained(MODEL_NAME)

In [3]:
import torch

In [4]:
loaded_quantized_model = torch.jit.load("gaepago-20-lite/model_quant_int8.pt")

## 모델결과

In [9]:
preds = []
gts = []
# quant_logits_list = []
for i in range(len(test_data)):
    inputs = feature_extractor(test_data[i]["audio"]["array"], sampling_rate=sampling_rate, return_tensors="pt")
    with torch.no_grad():
        logits = loaded_quantized_model(**inputs)['logits']
#     quant_logits_list.append(logits)
    predicted_class_ids = torch.argmax(logits).item()
    predicted_label = config.id2label[predicted_class_ids]
    preds.append(predicted_label)
    gts.append(config.id2label[test_data[i]['label']])

In [10]:
from sklearn.metrics import classification_report
test_performance = classification_report(gts, preds,digits=4)
print(test_performance)

              precision    recall  f1-score   support

        bark     0.5556    0.6250    0.5882         8
    growling     1.0000    0.8333    0.9091         6
        howl     0.7500    0.8571    0.8000         7
     panting     1.0000    0.8000    0.8889        10
     whimper     0.3750    0.4286    0.4000         7

    accuracy                         0.7105        38
   macro avg     0.7361    0.7088    0.7172        38
weighted avg     0.7452    0.7105    0.7224        38

